In [1]:
print('hello world')

hello world


In [2]:
import sys
sys.path.append('/home/s94zalek/shape_matching')

from datasets_code import build_dataloader, build_dataset
from utils.options import parse_options
from train import create_train_val_dataloader
import torch
import numpy as np

import os
os.chdir('/home/s94zalek/shape_matching')

# print current working directory
print(os.getcwd())

Jupyter environment detected. Enabling Open3D WebVisualizer.
[Open3D INFO] WebRTC GUI backend enabled.
[Open3D INFO] WebRTCWindowSystem: HTTP handshake server disabled.
/home/s94zalek/shape_matching


In [3]:
import os

# root_path = osp.abspath(osp.join(__file__, osp.pardir))
root_path = '/home/s94zalek/shape_matching'

opt = parse_options(root_path, is_train=False, use_argparse=False,
                    opt_path = 'options/train/faust.yaml')

opt['root_path'] = root_path
opt['dist'] = False

opt['datasets']['train_dataset']['return_corr'] = True
opt['datasets']['train_dataset']['return_dist'] = False
opt['datasets']['test_dataset']['return_dist'] = False

# create train and validation dataloaders
result = create_train_val_dataloader(opt)
train_loader, train_sampler, val_loader, total_epochs, total_iters = result
train_set = train_loader.dataset

test_set = build_dataset(opt['datasets']['test_dataset'])
test_loader = build_dataloader(
test_set, opt['datasets']['test_dataset'], phase='val', num_gpu=opt['num_gpu'], dist=opt['dist'], sampler=None, seed=opt['manual_seed'])


Backend DataParallel.
Path already exists. Rename it to /home/s94zalek/shape_matching/results/faust_archived_20240425_132207


Calculating functional maps: 100%|███████████████████████████████████████████████████████████████████████████████████| 400/400 [00:04<00:00, 94.69it/s]
/home/s94zalek/.conda/envs/fmnet/lib/python3.8/site-packages/torch/utils/data/dataloader.py:558: UserWarning: This DataLoader will create 16 worker processes in total. Our suggested max number of worker in current system is 8, which is smaller than what this DataLoader is going to create. Please be aware that excessive worker creation might get DataLoader running slow or even freeze, lower the worker number to avoid potential slowness/freeze if necessary.
  warnings.warn(_create_warning_msg(
Calculating functional maps: 100%|███████████████████████████████████████████████████████████████████████████████████| 400/400 [00:04<00:00, 88.12it/s]


In [11]:
import trimesh

scene = trimesh.Scene()

In [38]:
def plot_lb_evecs(data_to_plot, evecs_indices, scene):
    
    scene.geometry.clear()
    
    # concat all eigenvectors of interest
    evecs_concat = torch.tensor([])
    for i in evecs_indices:
        evecs = data_to_plot['evecs'][:, i]
        evecs_concat = torch.cat((evecs_concat, evecs), 0)
        
    # make a color map with min/max values consistent for all shapes        
    cmap = trimesh.visual.color.interpolate(evecs_concat, 'bwr')

    # plot the meshes
    curr_vert = 0
    for i, _ in enumerate(evecs_indices):
        mesh = trimesh.Trimesh(
            vertices=data_to_plot['verts'].cpu().numpy() + np.array([i * 1, 0, 0]),
            faces=data_to_plot['faces'].cpu().numpy()
            )

        mesh.visual.vertex_colors = cmap[curr_vert:curr_vert + len(mesh.vertices)]
        curr_vert += len(mesh.vertices)
        scene.add_geometry(mesh)

In [39]:
plot_lb_evecs(
    data_to_plot=train_set[0]['first'],
    evecs_indices=range(5, 10),
    scene=scene
)
scene.show()

In [40]:
plot_lb_evecs(
    data_to_plot=train_set[0]['first'],
    evecs_indices=range(185, 190),
    scene=scene
)
scene.show()

In [53]:
plot_lb_evecs(
    data_to_plot=train_set[17 * 81]['first'],
    evecs_indices=range(5, 10),
    scene=scene
)
scene.show()

In [54]:
plot_lb_evecs(
    data_to_plot=train_set[17 * 81]['first'],
    evecs_indices=range(185, 190),
    scene=scene
)
scene.show()

# TODO
Run difference operators on WKS descriptors